# Compare Sentinel-5P O3 profile against lidar

See also https://mpc-vdaf-server.tropomi.eu/o3-profile/o3-profile-offl-lidar/hohenpeissenberg

In [ ]:
import avl
import harp

In [ ]:
!ls s5p

In [ ]:
print(harp.import_product("s5p/S5P_RPRO_L2VOO3__PR_20220301T105407_20220301T123537_22701_03_020400_20230327T082409_hohenpeissenberg.nc"))

In [ ]:
!ls lidar

In [ ]:
print(harp.import_product("lidar/groundbased_lidar.o3_dwd001_hohenpeissenberg_20220228t181711z_20220301t050741z_001.hdf"))

In [ ]:
!harpcollocate -d 'datetime 24 [h]' --point-in-area-yx -aa 'valid(O3_column_number_density);validity !& 255' -nx datetime -ny datetime s5p lidar collocations.csv

In [ ]:
!cat collocations.csv

In [ ]:
operations = ";".join([
    'collocate_left("collocations.csv")',
    "exclude(cloud_albedo, surface_albedo, wavelength)",
    "derive(datetime {time} [days since 2000-01-01])",
    "derive(altitude [km])",
    "derive(pressure [hPa])",
    "derive(O3_column_number_density [DU])",
    "derive(O3_column_number_density_uncertainty [DU])",
    "derive(O3_number_density [Tmolec/cm3])",
    "derive(O3_number_density_uncertainty [Tmolec/cm3])",
    "derive(O3_number_density_dfs {time})",
    "derive(tropopause_altitude {time} [km])",
    "derive(area {time} [km2])",
])
post_operations = "sort(collocation_index)"
s5p_collocated = harp.import_product("s5p/*", operations, post_operations=post_operations)
print(s5p_collocated)

In [ ]:
operations = ";".join([
    'collocate_right("collocations.csv")',
    "derive(datetime {time} [days since 2000-01-01])",
    "derive(latitude {time})",
    "derive(longitude {time})",
    "derive(O3_column_number_density {time} [DU])",
    "derive(O3_number_density {time,vertical} [Tmolec/cm3])",
    "derive(tropopause_altitude {time} [km])",
])
post_operations = "sort(collocation_index)"
lidar_collocated = harp.import_product("lidar/*", operations, post_operations=post_operations)
print(lidar_collocated)

In [ ]:
operations = ";".join([
    "exclude(O3_column_number_density,O3_column_number_density_uncertainty)",
    "regrid(vertical, altitude [km], (16.5,18.25,20,21.75,23.75,25.5,27.5,29.25,31.25,33.25,35.25,37.25,39.5,41,43.75), "
        "(15.5,17.375,19.125,20.875,22.75,24.625,26.5,28.375,30.25,32.25,34.25,36.25,38.375,40.25,42.375,44.875))",
    "derive(O3_column_number_density {time} [DU])",  # recalculate the total column using the revised grid
    "squash(time, altitude)",
])
s5p = harp.execute_operations(s5p_collocated, operations)
print(s5p)

In [ ]:
lidar = harp.execute_operations(lidar_collocated, operations)
print(lidar)

In [ ]:
harp.export_product(s5p, "s5p.nc")
harp.export_product(lidar, "lidar.nc")

In [ ]:
avl.Heatmap(s5p, value="O3_number_density", colormap="davos", colorrange=(0,6))

In [ ]:
avl.Heatmap(lidar, value="O3_number_density", colormap="davos", colorrange=(0,6))

In [ ]:
avl.vis.Heatmap(
    data=s5p.O3_number_density.data - lidar.O3_number_density.data,
    coords=[avl.get_timestamps(s5p.datetime), s5p.altitude.data],
    xlabel="time", ylabel="altitude (km)", colorlabel="Tmolec/cm3", title="O3 number density SAT-REF",
    colormap="RdBu_r", colorrange=(-3,3)
)

In [ ]:
plot = avl.vis.Plot()
plot.add(avl.Scatter(s5p, value="O3_column_number_density"))
plot.add(avl.Scatter(lidar, value="O3_column_number_density"))
plot

In [ ]:
avl.vis.Scatter(
    xdata=avl.get_timestamps(s5p.datetime),
    ydata=s5p.O3_column_number_density.data - lidar.O3_column_number_density.data,
    title="O3 difference (S5P - lidar)"
)